# Split big geojson into regions

## Setup

In [1]:
import pandas as pd
import numpy as np

# For importing geojson:
import json

# For saving new geojson:
from geojson import FeatureCollection

# For drawing maps:
import folium
from folium import plugins

## Import data

In [2]:
df_regions = pd.read_csv('./LSOA_regions.csv')

df_regions.head()

LSOA11CD   LSOA11NM    CCG19CD                      CCG19NM    STP19CD  \
0  E01031349  Adur 001A  E38000213  NHS Coastal West Sussex CCG  E54000033   
1  E01031350  Adur 001B  E38000213  NHS Coastal West Sussex CCG  E54000033   
2  E01031351  Adur 001C  E38000213  NHS Coastal West Sussex CCG  E54000033   
3  E01031352  Adur 001D  E38000213  NHS Coastal West Sussex CCG  E54000033   
4  E01031370  Adur 001E  E38000213  NHS Coastal West Sussex CCG  E54000033   

                  STP19NM LHB20CD LHB20NM LHB20NMW    RGN11CD     RGN11NM  
0  Sussex and East Surrey     NaN     NaN      NaN  E12000008  South East  
1  Sussex and East Surrey     NaN     NaN      NaN  E12000008  South East  
2  Sussex and East Surrey     NaN     NaN      NaN  E12000008  South East  
3  Sussex and East Surrey     NaN     NaN      NaN  E12000008  South East  
4  Sussex and East Surrey     NaN     NaN      NaN  E12000008  South East

Find all of the unique STP codes and LHB codes:

In [3]:
STP_code_set = set(df_regions['STP19CD'])
# Remove NaN values from Welsh LSOAs:
STP_code_set = [STP_code for STP_code in STP_code_set if isinstance(STP_code, str)]
# Sort alphabetically:
STP_code_set = sorted(list(STP_code_set))

STP_code_set

['E54000005',
 'E54000006',
 'E54000007',
 'E54000008',
 'E54000009',
 'E54000010',
 'E54000011',
 'E54000012',
 'E54000013',
 'E54000014',
 'E54000015',
 'E54000016',
 'E54000017',
 'E54000018',
 'E54000019',
 'E54000020',
 'E54000021',
 'E54000022',
 'E54000023',
 'E54000024',
 'E54000025',
 'E54000026',
 'E54000027',
 'E54000028',
 'E54000029',
 'E54000030',
 'E54000031',
 'E54000032',
 'E54000033',
 'E54000034',
 'E54000035',
 'E54000036',
 'E54000037',
 'E54000038',
 'E54000039',
 'E54000040',
 'E54000041',
 'E54000042',
 'E54000043',
 'E54000044',
 'E54000048',
 'E54000049']

In [4]:
LHB_code_set = set(df_regions['LHB20CD'])
# Remove NaN values from English LSOAs:
LHB_code_set = [LHB_code for LHB_code in LHB_code_set if isinstance(LHB_code, str)]
# Sort alphabetically:
LHB_code_set = sorted(list(LHB_code_set))

LHB_code_set

['W11000023',
 'W11000024',
 'W11000025',
 'W11000028',
 'W11000029',
 'W11000030',
 'W11000031']

For each of these STP and LHB codes, find the LSOAs that belong to it:

In [5]:
# Record these for info or naming of the .geojson files:
code_dict = {}
group_dict = {}

# Record these just out of interest:
region_name_list = []
group_name_list = []
n_lsoas_list = []

# English LSOAs:
for STP in STP_code_set:
    df_regions_stp = df_regions[df_regions['STP19CD'] == STP]
    LSOA_codes_for_this_stp = df_regions_stp['LSOA11CD'].values
    
    code_dict[STP] = LSOA_codes_for_this_stp
    
    group_name = df_regions_stp['STP19NM'].iloc[0]
    group_dict[STP] = group_name
    
    region_name = df_regions_stp['RGN11NM'].iloc[0]
    
    # Update lists for the dataframe:
    region_name_list.append(region_name)
    group_name_list.append(group_name)
    n_lsoas_list.append(len(LSOA_codes_for_this_stp))
    
# Welsh LSOAs:
for LHB in LHB_code_set:
    df_regions_lhb = df_regions[df_regions['LHB20CD'] == LHB]
    LSOA_codes_for_this_lhb = df_regions_lhb['LSOA11CD'].values
    
    code_dict[LHB] = LSOA_codes_for_this_lhb
    
    group_name = df_regions_lhb['LHB20NM'].iloc[0]
    group_dict[LHB] = group_name
    
    region_name = df_regions_lhb['RGN11NM'].iloc[0]
    
    # Update lists for the dataframe:
    region_name_list.append(region_name)
    group_name_list.append(group_name)
    n_lsoas_list.append(len(LSOA_codes_for_this_lhb))

In [6]:
pd.DataFrame(
    np.stack([region_name_list, group_name_list, n_lsoas_list], axis=-1),
    columns=['Region', 'Group', 'Number of LSOAs']
)

Region  \
0   Yorkshire and The Humber   
1   Yorkshire and The Humber   
2                 North West   
3                 North West   
4   Yorkshire and The Humber   
5              West Midlands   
6              West Midlands   
7              East Midlands   
8              East Midlands   
9              East Midlands   
10             East Midlands   
11             West Midlands   
12             West Midlands   
13             West Midlands   
14             West Midlands   
15             East Midlands   
16           East of England   
17           East of England   
18           East of England   
19                South East   
20           East of England   
21           East of England   
22                    London   
23                    London   
24                    London   
25                    London   
26                    London   
27                South East   
28                South East   
29                South East   
30                South East   
31                South West   
32                South West   
33                South West   
34                South West   
35                South West   
36                South West   
37                South East   
38                South West   
39                South East   
40                North West   
41                North West   
42                     Wales   
43                     Wales   
44                     Wales   
45                     Wales   
46                     Wales   
47                     Wales   
48                     Wales   

                                                Group Number of LSOAs  
0   West Yorkshire and Harrogate (Health and Care ...            1521  
1                              Humber, Coast and Vale             845  
2   Greater Manchester Health and Social Care Part...            1694  
3                             Cheshire and Merseyside            1562  
4                       South Yorkshire and Bassetlaw             923  
5                    Staffordshire and Stoke on Trent             687  
6                   Shropshire and Telford and Wrekin             301  
7                           Joined Up Care Derbyshire             621  
8                                        Lincolnshire             420  
9      Nottingham and Nottinghamshire Health and Care             609  
10              Leicester, Leicestershire and Rutland             611  
11              The Black Country and West Birmingham             804  
12                            Birmingham and Solihull             681  
13                          Coventry and Warwickshire             534  
14                   Herefordshire and Worcestershire             480  
15                                   Northamptonshire             413  
16                    Cambridgeshire and Peterborough             507  
17    Norfolk and Waveney Health and Care Partnership             611  
18                       Suffolk and North East Essex             562  
19              Bedfordshire, Luton and Milton Keynes             537  
20                       Hertfordshire and West Essex             857  
21                                Mid and South Essex             705  
22      North West London Health and Care Partnership            1153  
23           North London Partners in Health and Care             795  
24            East London Health and Care Partnership            1023  
25                    Our Healthier South East London            1007  
26      South West London Health and Care Partnership             857  
27                                    Kent and Medway            1065  
28                             Sussex and East Surrey            1104  
29                                     Frimley Health             440  
30                                  Surrey Heartlands             509  
31                   Cornwall and the Isles of Scilly             326  
32                                           

## Examine the big .geojson

What order are the LSOA shapes stored in? It seems to be sorted by LSOA11CD.

In [7]:
with open('./LSOA_2011.geojson') as f:
    geojson_ew = json.load(f)

In [8]:
geojson_ew

{'type': 'FeatureCollection',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'LSOA11CD': 'E01000001',
    'LSOA11NM': 'City of London 001A',
    'LSOA11NMW': 'City of London 001A'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-0.097288715347549, 51.52157704785546],
      [-0.096515642542932, 51.52027437100127],
      [-0.095269034842215, 51.52050198646577],
      [-0.094770564012461, 51.520594346469125],
      [-0.094392974221931, 51.52066936131822],
      [-0.094504708025394, 51.51975924201876],
      [-0.09529429505753, 51.5189257778207],
      [-0.095083736973573, 51.51823695504652],
      [-0.09593354571175, 51.51675279228869],
      [-0.094943290436749, 51.516586509742694],
      [-0.095481176694217, 51.51544002548439],
      [-0.095797241748603, 51.514967104049326],
      [-0.096588885445263, 51.51484127077235],
      [-0.097983152973857, 51.51553692809937],
      [-0.0978541880

In [9]:
geojson_ew.keys()

dict_keys(['type', 'crs', 'features'])

In [10]:
big_geojson_order = []

for i in range(len(geojson_ew['features'])):
    big_geojson_order.append(geojson_ew['features'][i]['properties']['LSOA11CD'])

In [11]:
geojson_ew['features']

[{'type': 'Feature',
  'properties': {'LSOA11CD': 'E01000001',
   'LSOA11NM': 'City of London 001A',
   'LSOA11NMW': 'City of London 001A'},
  'geometry': {'type': 'Polygon',
   'coordinates': [[[-0.097288715347549, 51.52157704785546],
     [-0.096515642542932, 51.52027437100127],
     [-0.095269034842215, 51.52050198646577],
     [-0.094770564012461, 51.520594346469125],
     [-0.094392974221931, 51.52066936131822],
     [-0.094504708025394, 51.51975924201876],
     [-0.09529429505753, 51.5189257778207],
     [-0.095083736973573, 51.51823695504652],
     [-0.09593354571175, 51.51675279228869],
     [-0.094943290436749, 51.516586509742694],
     [-0.095481176694217, 51.51544002548439],
     [-0.095797241748603, 51.514967104049326],
     [-0.096588885445263, 51.51484127077235],
     [-0.097983152973857, 51.51553692809937],
     [-0.097854188061043, 51.516600031432134],
     [-0.099748844563837, 51.51676760039035],
     [-0.099669100609672, 51.517450020863116],
     [-0.099166091802661, 

In [12]:
big_geojson_order

['E01000001',
 'E01000002',
 'E01000003',
 'E01000005',
 'E01000006',
 'E01000007',
 'E01000008',
 'E01000009',
 'E01000010',
 'E01000011',
 'E01000012',
 'E01000013',
 'E01000014',
 'E01000015',
 'E01000016',
 'E01000017',
 'E01000018',
 'E01000019',
 'E01000020',
 'E01000021',
 'E01000022',
 'E01000023',
 'E01000024',
 'E01000025',
 'E01000027',
 'E01000028',
 'E01000029',
 'E01000030',
 'E01000031',
 'E01000032',
 'E01000033',
 'E01000034',
 'E01000035',
 'E01000036',
 'E01000037',
 'E01000038',
 'E01000039',
 'E01000040',
 'E01000041',
 'E01000042',
 'E01000043',
 'E01000044',
 'E01000045',
 'E01000046',
 'E01000048',
 'E01000049',
 'E01000050',
 'E01000051',
 'E01000052',
 'E01000053',
 'E01000054',
 'E01000055',
 'E01000056',
 'E01000057',
 'E01000058',
 'E01000059',
 'E01000060',
 'E01000061',
 'E01000062',
 'E01000063',
 'E01000064',
 'E01000065',
 'E01000066',
 'E01000067',
 'E01000068',
 'E01000069',
 'E01000070',
 'E01000071',
 'E01000072',
 'E01000073',
 'E01000074',
 'E010

## Match big .geojson info with regions

In [13]:
for group in code_dict.keys():
    lsoa_here = code_dict[group]
    features_here = []
    for lsoa in lsoa_here:
        # Find where it is in the big geojson:
        try:
            ind = big_geojson_order.index(lsoa)
            # inds_for_geojson.append(ind)
            features_here.append(geojson_ew['features'][ind])
        except ValueError:
            print(f'Problem with {group}, LSOA {lsoa}')
    
    features_here = FeatureCollection(features_here)
            
#     geojson_here = {}
#     geojson_here['type'] = geojson_ew['type']
#     geojson_here['crs'] = geojson_ew['crs']
#     geojson_here['features'] = features_here
    
    # Now save the file as something new:
    group_name = group_dict[group]
    group_name = group_name.replace(' ', '~')
    save_name = 'LSOA_' + group_name + '.geojson'
    
    with open('./region_geojson/'+save_name, 'w', encoding='utf-8') as f:
        json.dump(features_here, f, ensure_ascii=False)

### Import one of the newly-made .geojson

In [14]:
with open('./region_geojson/LSOA_Devon.geojson') as f:
    geojson_devon = json.load(f)

In [15]:
# Create a map
devon_map = folium.Map(location=[50.7, -4],
                        zoom_start=9,
                        tiles='cartodbpositron')
# Add choropleth
folium.Choropleth(geo_data=geojson_devon,
                  highlight=True).add_to(devon_map)

# Generate map
devon_map